## <font color = "lightseagreen">0. Importing libraries<font>

In [1]:
import pandas as pd
import numpy as np
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
import time

## <font color = "lightseagreen">1. Inputing credentials<font>

In [2]:
sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id="af3a4e21d9974f798b0ddef081728f2b",
                                                           client_secret="99a65d20eff04d64bcf24b11824dffc4"))

## <font color = "lightseagreen">3. Extracting songs and audio features<font>

In [20]:
# Initially there were 17 playlists. Attempting to make it so I can finally download my data without problems I am cutting down on number of everything...
# from "Discover" tag jazz vibes
playlist_ids = ["37i9dQZF1DX0SM0LYsmbMT"]
tracks = []

# function used in class to extract tracks' info from a list
def get_playlist_tracks(username, playlist_id):
    
    results = sp.user_playlist_tracks(username, playlist_id)
    tracks = results['items']
    
    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])
    
    return tracks

In [21]:
# a list to store the names of the artists
artists = []
artist_ids = []

# a loop that will go through the list and store the artists' names in their respective list
for playlist_id in playlist_ids:
    i = 0
    tracks.append(get_playlist_tracks("spotify", playlist_id))

    # the tracks list is a list of 9 nested lists of tracks, each of which contains as many dictionaries as there are tracks in the playlists, with information about said tracks
    # what is needed for now, however, is the name of the artists, thus this is what will be extracted
    for l in range(0, len(tracks[i]) - 1):
        artists.append(tracks[i][l]["track"]["artists"][0]["name"])
        artist_ids.append(tracks[i][l]["track"]["artists"][0]["id"])
    i += 1

print("Artist Names:", len(artists))
print("Artist Ids:", len(artist_ids))

Artist Names: 299
Artist Ids: 299


In [22]:
# listed track info, along with the info regarding the artists is contained in nested dictionaries
tracks[0][0]["track"]["artists"]#[0]#["id"]

[{'external_urls': {'spotify': 'https://open.spotify.com/artist/4EOKoMTIR7K71Skv7gAmgS'},
  'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS',
  'id': '4EOKoMTIR7K71Skv7gAmgS',
  'name': 'Platinum Dust',
  'type': 'artist',
  'uri': 'spotify:artist:4EOKoMTIR7K71Skv7gAmgS'}]

In [23]:
# storing artist names and ids in a dataframe and checking dataframe for duplicates
artists_df = pd.DataFrame({"artist_name": artists, "artist_id": artist_ids})
artists_df.duplicated().sum()

122

<font color = "royalblue">There is a great number of duplicate rows (nothing unexpected, since many releases from each artist can be contained in the same or in multiple lists).</font>

In [24]:
# so this is a list of artists' names extracted from the the playlists above
artists_df = artists_df.drop_duplicates(keep="first", ignore_index=True)
artists_df

artist_name               artist_id
0    Platinum Dust  4EOKoMTIR7K71Skv7gAmgS
1          Knowsum  5n286gaq2TJok5XfBjSX7q
2            Civin  05PE7U7GPUq687RB2ZJdFW
3             FLKS  0su9f9WdmaeYFON6XEaXb0
4        Otis Neon  3GMuWlPjxsaDOInrqPP1k5
..             ...                     ...
172        Oh, My.  1f5I28sZb2efjRLXO1jX0h
173      Wezt MAAD  1hwXiwb02GgcXPuAewKCmF
174          Dpsht  2VhyMRukJ2e1CgZ6k7Tux3
175      Beta Beat  5om7d89XzwR16u36EyuRSk
176         Juliàn  2SJLGPoAJhy9Id6N8oAftk

[177 rows x 2 columns]

In [11]:
# function to extract albums of artists
def get_those_albums(artists_df):
    
    # to store the albums
    albums = []

    # getting albums
    for name in artists_df.artist_name:
        results_albums = sp.search(q = name, limit = 50, type = "album")
        albums.extend(results_albums["albums"]["items"])
        # extending the results beyond the upper limit of 50 supported by the .artist_albums function
        time.sleep(10)  # to avoid being denied to make more requests from the API
        while results_albums["albums"]["next"]:
            results_albums = sp.next(results_albums["albums"])
            albums.extend(results_albums["albums"]["items"])
        time.sleep(10)
    return albums


In [8]:
#### Alternative method to get albums using artist name with .artist_albums ####

""" # function to extract albums of artists
def get_those_albums(artists_df):
    
    # to store the albums
    albums = []

    # getting albums
    for id in artists_df.artist_id:
        results_albums = sp.artist_albums(id, limit=50)
        albums.extend(results_albums["items"])
        # extending the results beyond the upper limit of 50 supported by the .artist_albums function
        time.sleep(10)  # to avoid being denied to make more requests from the API
        while results_albums["next"]:
            results_albums = sp.next(results_albums)
            albums.extend(results_albums["items"])
        time.sleep(10)
    return albums

albums = get_those_albums(artists_df)
albums """

In [25]:
# running the function for the entirety of the artist ids collected ended up in a timeout error... making less requests than I actually would to finally finish this damned assignment...
albums = get_those_albums(artists_df[:10])
albums

[{'album_type': 'single',
  'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/4EOKoMTIR7K71Skv7gAmgS'},
    'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS',
    'id': '4EOKoMTIR7K71Skv7gAmgS',
    'name': 'Platinum Dust',
    'type': 'artist',
    'uri': 'spotify:artist:4EOKoMTIR7K71Skv7gAmgS'}],
  'available_markets': ['AD',
   'AE',
   'AG',
   'AL',
   'AM',
   'AO',
   'AR',
   'AT',
   'AU',
   'AZ',
   'BA',
   'BB',
   'BD',
   'BE',
   'BF',
   'BG',
   'BH',
   'BI',
   'BJ',
   'BN',
   'BO',
   'BR',
   'BS',
   'BT',
   'BW',
   'BY',
   'BZ',
   'CA',
   'CD',
   'CG',
   'CH',
   'CI',
   'CL',
   'CM',
   'CO',
   'CR',
   'CV',
   'CW',
   'CY',
   'CZ',
   'DE',
   'DJ',
   'DK',
   'DM',
   'DO',
   'DZ',
   'EC',
   'EE',
   'EG',
   'ES',
   'ET',
   'FI',
   'FJ',
   'FM',
   'FR',
   'GA',
   'GB',
   'GD',
   'GE',
   'GH',
   'GM',
   'GN',
   'GQ',
   'GR',
   'GT',
   'GW',
   'GY',
   'HK',
   'HN',
   'HR',
   'HT

In [26]:
len(albums)

1911

In [32]:
album_names = []

for album in albums:
    album_names.append(album["name"])

In [34]:
len(np.unique(album_names))

1728

<font color = "royalblue">As shown above, there are albums with the same name, which means that the method .search(q=<album name>, type="track") could not be used in this case, as it could cause errors. Thus and begrudgingly after the trouble it has caused, the use of the function .album_tracks() will be employed, but this time with breaks among requests and only 50 albums worth of ids<font>

In [42]:
""" album_dict = {"albums":albums}
albums_df = pd.DataFrame(album_dict)
albums_df.to_csv("albums_df.csv") """

In [39]:
# function to use album id to get tracks' ids and titles
def get_those_tracks(albums):
    
    track_names = []
    track_ids = []

    # getting tracks
    for album in albums:
        results_tracks = sp.album_tracks(album["id"], limit=50)
        for track in results_tracks["items"]:
            track_names.append(track["name"])
            track_ids.append(track["id"])
        time.sleep(10)
        
        # extending tracks' results
        while results_tracks["next"]:
            results_tracks = sp.next(results_tracks)
            for track in results_tracks["items"]:
                track_names.append(track["name"])
                track_ids.append(track["id"])
        time.sleep(10)
    return track_names, track_ids

In [40]:
title, track_id = get_those_tracks(albums[:50])
title

['Homecooking',
 'Winning At Life',
 'Count Basic',
 'Dizzy',
 'Part X',
 "It's Our Time",
 'Girls',
 'Platinum',
 'Little Red Wagon',
 "Smokin' and Drinkin' (feat. Little Big Town)",
 'Priscilla',
 'Automatic',
 'Bathroom Sink',
 'Old Sh!t',
 "All That's Left (feat. The Time Jumpers)",
 'Gravity Is a B**ch',
 "Babies Makin' Babies",
 "Somethin' Bad (with Carrie Underwood) - Duet with Carrie Underwood [Album]",
 'Holding On to You',
 'Two Rings Shy',
 'Hard Staying Sober',
 'Another Sunday in the South',
 'Team Burden',
 'Why You Think',
 'Sky Red',
 'Truth Be Told',
 'Red Lights',
 'Back From The Dead',
 'Pain Killers',
 'Mercedez',
 'Love Cycle',
 'Patek Water',
 'Down To Ride',
 'Choir Music',
 'Not Easy',
 'Other Side',
 'Like A Bird',
 'Sweet Hangover',
 "Why Don't You",
 'Truth Be Told',
 'Love Cycle',
 'Red Lights',
 '5 Stars',
 'Club House',
 'Reminiscing',
 'Mercedez',
 'Back From The Dead',
 'Why You Think',
 'Forever Paid',
 'Inside Out',
 'Got Her Own',
 'Down To Ride',
 'P

In [41]:
track_id

['3rr4I5VFW8TJebCkbrQK3N',
 '5zGhvl37kzqACtEnoVpdyz',
 '6BtRHhPR8PcfBBSAsY0ppd',
 '4jtGfSRuNkTBkF3I9qt0N5',
 '6r6IpMsJ2e6mpGmal4qLft',
 '4MeXAGHd3SYAgfx8YsTveT',
 '2VKDgn8FyQQBWQqu7BY6Va',
 '4r7AGbkZDeYII8J93kRcrY',
 '4sl4UWqzHSG7riBKdralwy',
 '13keyz9ikBe6ZpRasw7l4X',
 '2LYdjYaB15TYqS3uaNtiPy',
 '0B0y2FImat9j9MJTNRZWfW',
 '0YV73fsl9Wzlj61EPspjJ3',
 '7nRl82OQNxuZRQmg2T7OYN',
 '0DwndJCTTyGidd4ZXEzuk6',
 '3pnhahHXUFrQ8nQdeol6AV',
 '3ASmJaf3KaNWHgktGkPnF6',
 '6s9m5J92By7jii22Q2XtY2',
 '7A35lRz4cm0QkbnlNAJPtm',
 '65roP3ckjEoho56mOqjlP5',
 '4Tx8v6Otpoq8y6eQidW9BI',
 '0nb1lylqpHJsHfPUqHvpSN',
 '5o2LI57RSl9rQpf9KIs7s4',
 '3CnVpsqR58gfAp97m4ByuF',
 '7aQwtr0mg5YiiTr5aiK2t6',
 '2hzeDi6y5AeYhWWxmEzYyV',
 '340igUAkU3V48UrAbzwEci',
 '1Exon7Dr5v2PaizdrOCB89',
 '33UnAUIaCAXdrCQ4eCHlLu',
 '1RSCMALbPcI6ge6GSditdS',
 '4qkkL1BbQPcMkuWFlTctmk',
 '2rSCmymEVM7eFufOeeAX6d',
 '4n2AXWZbUsX42Lc6C9oF6k',
 '1ysJy8N10cMWrZnQXhTKYY',
 '2b9nRAHNWGMQkedVpjM1NP',
 '4KKL0uSQR1pPjczeNZR6Df',
 '3OTcXmVsChQzflumr0BtK8',
 

In [44]:
print("N_tracks", len(title))

N_tracks 438


In [45]:
track_dict = {"title": title, "track_id": track_id}
tracks_df = pd.DataFrame(track_dict)
# tracks_df.to_csv("tracks_df.csv")

In [43]:
# function to extract features
def fetch_me_those_sweet_feats(track_id):
    
    feat_results = []
    step_list = []

    # creating list of starting points to use in .audio_features()
    for i in range(0,(len(track_id)-1),100):
        step_list.append(i)

    for step in step_list:
        # conditionals will help set the exact ranges of values in track_ids to iterate upon
        # note: the function reads the index finishing at len(tracks_id) and NOT in len(tracks_id) - 1
        if step != step_list[-1]:
            for feature_set in sp.audio_features(track_id[step:(step+100)]):
                feat_results.append(feature_set)
        else:
            for feature_set in sp.audio_features(track_id[step:(len(track_id))]):
                feat_results.append(feature_set)
        time.sleep(10)
    return feat_results

In [46]:
### GETTING FEATURES ###
audio_features = fetch_me_those_sweet_feats(track_id)
audio_features

[{'danceability': 0.771,
  'energy': 0.361,
  'key': 2,
  'loudness': -8.882,
  'mode': 1,
  'speechiness': 0.136,
  'acousticness': 0.599,
  'instrumentalness': 0.917,
  'liveness': 0.353,
  'valence': 0.161,
  'tempo': 153.989,
  'type': 'audio_features',
  'id': '3rr4I5VFW8TJebCkbrQK3N',
  'uri': 'spotify:track:3rr4I5VFW8TJebCkbrQK3N',
  'track_href': 'https://api.spotify.com/v1/tracks/3rr4I5VFW8TJebCkbrQK3N',
  'analysis_url': 'https://api.spotify.com/v1/audio-analysis/3rr4I5VFW8TJebCkbrQK3N',
  'duration_ms': 131944,
  'time_signature': 4},
 {'danceability': 0.688,
  'energy': 0.232,
  'key': 4,
  'loudness': -13.083,
  'mode': 0,
  'speechiness': 0.154,
  'acousticness': 0.665,
  'instrumentalness': 0.863,
  'liveness': 0.256,
  'valence': 0.751,
  'tempo': 77.994,
  'type': 'audio_features',
  'id': '5zGhvl37kzqACtEnoVpdyz',
  'uri': 'spotify:track:5zGhvl37kzqACtEnoVpdyz',
  'track_href': 'https://api.spotify.com/v1/tracks/5zGhvl37kzqACtEnoVpdyz',
  'analysis_url': 'https://api.

In [78]:
audio_features

[{'danceability': 0.771,
  'energy': 0.361,
  'key': 2,
  'loudness': -8.882,
  'mode': 1,
  'speechiness': 0.136,
  'acousticness': 0.599,
  'instrumentalness': 0.917,
  'liveness': 0.353,
  'valence': 0.161,
  'tempo': 153.989,
  'type': 'audio_features',
  'id': '3rr4I5VFW8TJebCkbrQK3N',
  'uri': 'spotify:track:3rr4I5VFW8TJebCkbrQK3N',
  'track_href': 'https://api.spotify.com/v1/tracks/3rr4I5VFW8TJebCkbrQK3N',
  'analysis_url': 'https://api.spotify.com/v1/audio-analysis/3rr4I5VFW8TJebCkbrQK3N',
  'duration_ms': 131944,
  'time_signature': 4},
 {'danceability': 0.688,
  'energy': 0.232,
  'key': 4,
  'loudness': -13.083,
  'mode': 0,
  'speechiness': 0.154,
  'acousticness': 0.665,
  'instrumentalness': 0.863,
  'liveness': 0.256,
  'valence': 0.751,
  'tempo': 77.994,
  'type': 'audio_features',
  'id': '5zGhvl37kzqACtEnoVpdyz',
  'uri': 'spotify:track:5zGhvl37kzqACtEnoVpdyz',
  'track_href': 'https://api.spotify.com/v1/tracks/5zGhvl37kzqACtEnoVpdyz',
  'analysis_url': 'https://api.

In [82]:
# generating dataframe with the audio features extracted
features_df = pd.json_normalize(audio_features)
features_df

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0           0.771   0.361    2    -8.882     1       0.1360        0.5990   
1           0.688   0.232    4   -13.083     0       0.1540        0.6650   
2           0.677   0.310   10   -10.002     0       0.1300        0.5130   
3           0.700   0.434   10   -12.035     0       0.0371        0.2360   
4           0.700   0.373    5    -9.237     1       0.1980        0.0123   
..            ...     ...  ...       ...   ...          ...           ...   
433         0.532   0.878    7    -6.162     1       0.1160        0.0924   
434         0.316   0.363    1    -8.968     1       0.0339        0.1790   
435         0.125   0.372   11    -7.711     0       0.0368        0.2710   
436         0.319   0.694    2    -7.344     1       0.4810        0.3530   
437         0.739   0.750    0    -8.758     1       0.2780        0.0247   

     instrumentalness  liveness  valence    tempo            type  \
0             0.91700    0.3530   0.1610  153.989  audio_features   
1             0.86300    0.2560   0.7510   77.994  audio_features   
2             0.88500    0.5890   0.2350  148.117  audio_features   
3             0.92400    0.0954   0.5570   84.005  audio_features   
4             0.85900    0.1240   0.7190   82.068  audio_features   
..                ...       ...      ...      ...             ...   
433           0.02710    0.1780   0.0526  101.468  audio_features   
434           0.51100    0.0893   0.0542   90.087  audio_features   
435           0.75800    0.3260   0.0389  171.277  audio_features   
436           0.00346    0.3770   0.3820  195.618  audio_features   
437           0.00371    0.3130   0.7290  147.980  audio_features   

                         id                                   uri  \
0    3rr4I5VFW8TJebCkbrQK3N  spotify:track:3rr4I5VFW8TJebCkbrQK3N   
1    5zGhvl37kzqACtEnoVpdyz  spotify:track:5zGhvl37kzqACtEnoVpdyz   
2    6BtRHhPR8PcfBBSAsY0ppd  spotify:track:6BtRHhPR8PcfBBSAsY0ppd   
3    4jtGfSRuNkTBkF3I9qt0N5  spotify:track:4jtGfSRuNkTBkF3I9qt0N5   
4    6r6IpMsJ2e6mpGmal4qLft  spotify:track:6r6IpMsJ2e6mpGmal4qLft   
..                      ...                                   ...   
433  5eoZmMlKhQGErYAm5LrH7s  spotify:track:5eoZmMlKhQGErYAm5LrH7s   
434  0krZ8cTtvMnCGYT0sKM5z4  spotify:track:0krZ8cTtvMnCGYT0sKM5z4   
435  4Hn9CE6bkSZO7TicuRHpXt  spotify:track:4Hn9CE6bkSZO7TicuRHpXt   
436  2D79cav9guk3r4C6Al7dvp  spotify:track:2D79cav9guk3r4C6Al7dvp   
437  7yXEYGOZ7RknAG0NhxkrXj  spotify:track:7yXEYGOZ7RknAG0NhxkrXj   

                                            track_href  \
0    https://api.spotify.com/v1/tracks/3rr4I5VFW8TJ...   
1    https://api.spotify.com/v1/tracks/5zGhvl37kzqA...   
2    https://api.spotify.com/v1/tracks/6BtRHhPR8Pcf...   
3    https://api.spotify.com/v1/tracks/4jtGfSRuNkTB...   
4    https://api.spotify.com/v1/tracks/6r6IpMsJ2e6m...   
..                                                 ...   
433  https://api.spotify.com/v1/tracks/5eoZmMlKhQGE...   
434  https://api.spotify.com/v1/tracks/0krZ8cTtvMnC...   
435  https://api.spotify.com/v1/tracks/4Hn9CE6bkSZO...   
436  https://api.spotify.com/v1/tracks/2D79cav9guk3...   
437  https://api.spotify.com/v1/tracks/7yXEYGOZ7Rkn...   

                                          analysis_url  duration_ms  \
0    https://api.spotify.com/v1/audio-analysis/3rr4...       131944   
1    https://api.spotify.com/v1/audio-analysis/5zGh...       119265   
2    https://api.spotify.com/v1/audio-analysis/6BtR...       108069   
3    https://api.spotify.com/v1/audio-analysis/4jtG...        82131   
4    https://api.spotify.com/v1/audio-analysis/6r6I...       126707   
..                                                 ...          ...   
433  https://api.spotify.com/v1/audio-analysis/5eoZ...       297273   
434  https://api.spotify.com/v1/audio-analysis/0krZ...       305789   
435  https://api.spotify.com/v1/audio-analysis/4Hn9...       301061   
436  https://ap

<font color = "royalblue">The dataframe consists of 438 rows and 18 columns. The column type only refers to the type of information contained in each ot the dictionaries of the list audio_features and will not be needed going forth. It stands to reason that each row refers to each track, the id of which was used to extrach it from Spotify. Thus, the dataframes tracks_df and features_df will be merged.<font>

In [7]:
features_df = features_df.drop("type", axis=1)

In [8]:
audio_features_df = pd.concat([tracks_df, features_df], axis = 1)
audio_features_df

title                track_id  danceability  energy  key  \
0        Homecooking  3rr4I5VFW8TJebCkbrQK3N         0.771   0.361    2   
1    Winning At Life  5zGhvl37kzqACtEnoVpdyz         0.688   0.232    4   
2        Count Basic  6BtRHhPR8PcfBBSAsY0ppd         0.677   0.310   10   
3              Dizzy  4jtGfSRuNkTBkF3I9qt0N5         0.700   0.434   10   
4             Part X  6r6IpMsJ2e6mpGmal4qLft         0.700   0.373    5   
..               ...                     ...           ...     ...  ...   
433         Militant  5eoZmMlKhQGErYAm5LrH7s         0.532   0.878    7   
434    Positive Flow  0krZ8cTtvMnCGYT0sKM5z4         0.316   0.363    1   
435           Deeper  4Hn9CE6bkSZO7TicuRHpXt         0.125   0.372   11   
436  Millennial Rain  2D79cav9guk3r4C6Al7dvp         0.319   0.694    2   
437           Freeze  7yXEYGOZ7RknAG0NhxkrXj         0.739   0.750    0   

     loudness  mode  speechiness  acousticness  instrumentalness  liveness  \
0      -8.882     1       0.1360        0.5990           0.91700    0.3530   
1     -13.083     0       0.1540        0.6650           0.86300    0.2560   
2     -10.002     0       0.1300        0.5130           0.88500    0.5890   
3     -12.035     0       0.0371        0.2360           0.92400    0.0954   
4      -9.237     1       0.1980        0.0123           0.85900    0.1240   
..        ...   ...          ...           ...               ...       ...   
433    -6.162     1       0.1160        0.0924           0.02710    0.1780   
434    -8.968     1       0.0339        0.1790           0.51100    0.0893   
435    -7.711     0       0.0368        0.2710           0.75800    0.3260   
436    -7.344     1       0.4810        0.3530           0.00346    0.3770   
437    -8.758     1       0.2780        0.0247           0.00371    0.3130   

     valence    tempo                      id  \
0     0.1610  153.989  3rr4I5VFW8TJebCkbrQK3N   
1     0.7510   77.994  5zGhvl37kzqACtEnoVpdyz   
2     0.2350  148.117  6BtRHhPR8PcfBBSAsY0ppd   
3     0.5570   84.005  4jtGfSRuNkTBkF3I9qt0N5   
4     0.7190   82.068  6r6IpMsJ2e6mpGmal4qLft   
..       ...      ...                     ...   
433   0.0526  101.468  5eoZmMlKhQGErYAm5LrH7s   
434   0.0542   90.087  0krZ8cTtvMnCGYT0sKM5z4   
435   0.0389  171.277  4Hn9CE6bkSZO7TicuRHpXt   
436   0.3820  195.618  2D79cav9guk3r4C6Al7dvp   
437   0.7290  147.980  7yXEYGOZ7RknAG0NhxkrXj   

                                      uri  \
0    spotify:track:3rr4I5VFW8TJebCkbrQK3N   
1    spotify:track:5zGhvl37kzqACtEnoVpdyz   
2    spotify:track:6BtRHhPR8PcfBBSAsY0ppd   
3    spotify:track:4jtGfSRuNkTBkF3I9qt0N5   
4    spotify:track:6r6IpMsJ2e6mpGmal4qLft   
..                                    ...   
433  spotify:track:5eoZmMlKhQGErYAm5LrH7s   
434  spotify:track:0krZ8cTtvMnCGYT0sKM5z4   
435  spotify:track:4Hn9CE6bkSZO7TicuRHpXt   
436  spotify:track:2D79cav9guk3r4C6Al7dvp   
437  spotify:track:7yXEYGOZ7RknAG0NhxkrXj   

                                            track_href  \
0    https://api.spotify.com/v1/tracks/3rr4I5VFW8TJ...   
1    https://api.spotify.com/v1/tracks/5zGhvl37kzqA...   
2    https://api.spotify.com/v1/tracks/6BtRHhPR8Pcf...   
3    https://api.spotify.com/v1/tracks/4jtGfSRuNkTB...   
4    https://api.spotify.com/v1/tracks/6r6IpMsJ2e6m...   
..                                                 ...   
433  https://api.spotify.com/v1/tracks/5eoZmMlKhQGE...   
434  https://api.spotify.com/v1/tracks/0krZ8cTtvMnC...   
435  https://api.spotify.com/v1/tracks/4Hn9CE6bkSZO...   
436  https://api.spotify.com/v1/tracks/2D79cav9guk3...   
437  https://api.spotify.com/v1/tracks/7yXEYGOZ7Rkn...   

                                          analysis_url  duration_ms  \
0    https://api.spotify.com/v1/audio-analysis/3rr4...       131944   
1    https://api.spotify.com/v1/audio-analysis/5zGh...       119265   
2    https://api.spotify.com/v1/audio-analysis/6BtR...       108069   
3    https://api.spotify.com/v1/audio-analysis/4jtG...        8213

In [10]:
# checking for nans
audio_features_df.isna().sum()

title               0
track_id            0
danceability        0
energy              0
key                 0
loudness            0
mode                0
speechiness         0
acousticness        0
instrumentalness    0
liveness            0
valence             0
tempo               0
id                  0
uri                 0
track_href          0
analysis_url        0
duration_ms         0
time_signature      0
dtype: int64

In [12]:
# checking for white spaces
for col in audio_features_df.columns:
    print(col, len(audio_features_df[audio_features_df[col] == " "]))

title 0
track_id 0
danceability 0
energy 0
key 0
loudness 0
mode 0
speechiness 0
acousticness 0
instrumentalness 0
liveness 0
valence 0
tempo 0
id 0
uri 0
track_href 0
analysis_url 0
duration_ms 0
time_signature 0


In [9]:
#audio_features_df.to_csv("audio_features.csv")